In [5]:
##########################################################################################################################################
'''
    File name: allcodes3d.ipynb
    File version: 2.0.0
    Created by: Caroline Karina Chandra
    Project: Advanced Research Lab (ARL), WiSe 20/21
    Date created: December 1, 2020
    Last modified: April 19, 2021
    Python version: 3.8
'''
##########################################################################################################################################
__author__     = "Caroline Karina Chandra"
__credits__    = ["Caroline Karina Chandra", "Imants Dirba"]
__maintainer__ = "Caroline Karina Chandra"
__contacts__   = ["caroline.k.chandra@gmail.com", "carolinekarina.chandra@stud.tu-darmstadt.de", "karin001207@yahoo.com"]
__version__    = "2.0.0"
__status__     = "Development"
##########################################################################################################################################

import ipywidgets as wg
from IPython.display import display
import matplotlib.pyplot as plt
from matplotlib.lines import Line2D
from matplotlib.offsetbox import AnchoredText
from ipywidgets import HBox, VBox, Checkbox, ToggleButton
from mpl_toolkits.mplot3d import Axes3D
from matplotlib import cm
from matplotlib.ticker import LinearLocator, FormatStrFormatter
%matplotlib widget
%run etc.ipynb

In [3]:
def plotanything(dim):
    if dim == '2D':
        def choosex(x):
            if x == 'select x':
                optiony = ['select x']
            elif x == 'Diameter dp [nm]':
                optiony = ['select y', 'Relaxation time [s]', 'SAR [W/g]']
            elif x == 'Frequency f [kHz]':
                optiony = ['select y', 'SAR [W/g]']
            elif x == 'Field H [G]':
                optiony = ['select y', 'SAR [W/g]']
            def choosey(y):
                if y == 'Relaxation time [s]':
                    Material=wg.Text(value='Material', placeholder='Type material', disabled=False, layout=wg.Layout(width='120px', height='30px'))
                    Ku     = wg.BoundedFloatText(value=48, min=1, max=6600, step=0.1, disabled=False, layout=wg.Layout(width='100px', height='25px'))
                    Kuout  = wg.Output()
                    Medium = wg.Text(value='Medium', placeholder='Type medium', disabled=False, layout=wg.Layout(width='120px', height='30px'))
                    ds     = wg.BoundedFloatText(value=2.50, min=0, max=25, step=0.01, disabled=False, layout=wg.Layout(width='100px', height='25px'))
                    dsout  = wg.Output()
                    eta    = wg.BoundedFloatText(value=1e-3, min=1e-4, max=1e3, step=1e-4, disabled=False, layout=wg.Layout(width='100px', height='25px'))
                    etaout = wg.Output()
                    
                    Mattext = wg.Label('Material :')
                    Medtext = wg.Label('Medium :')
                    Kutext  = wg.Label(r'Anisotropy constant $K_u$ [kJ/m3] :')
                    dstext  = wg.Label(r'Surfactant layer thickness $d_s$ [nm] :')
                    etatext = wg.Label(r'Viscosity $\eta$ [Ns/m2] :')

                    space  = wg.Label(r'$\quad$')
                    
                    plotbutton = wg.Button(description='Plot!', tooltip='Click this to plot')
                    plotbuttonout = wg.Output()

                    display(HBox((VBox((Mattext, Medtext)),
                                  VBox((Material, Medium)), space,
                                  VBox((Kutext, dstext)),
                                  VBox((Ku, Kuout, ds, dsout)), space,
                                  VBox((space, etatext)),
                                  VBox((space, eta, etaout)), space,
                                  VBox((space, plotbutton)) )) )
                    display(plotbuttonout)
                    
                    def on_button_clicked(plot):
                        with plotbuttonout:
                            siKu  = float(Ku.value  * unit['Factor']['Anisotropy constant'])
                            sieta = float(eta.value * unit['Factor']['Viscosity'])
                            sids  = float(ds.value  * unit['Factor']['Surfactant layer thickness'])
                            
                            maxdia = ((6 * kb * T * np.log(1e50)) / (siKu * np.pi))**(1/3) * 1e9
                            dia = np.arange(1, maxdia, 0.05) * 1e-9
                            tn = tau0 * ((siKu * np.pi * dia**3) / (6 * kb * T))**(-0.5) * np.exp((siKu * np.pi * dia**3) / (6 * kb * T))
#                             tn = tau0 * np.exp((siKu * np.pi * dia**3) / (6 * kb * T))
                            tb = (sieta * np.pi * (dia + sids)**3) / (2 * kb * T)
                            tau = (tn * tb) / (tn + tb)

                            fig, ax = plt.subplots()
                            taun = ax.plot(dia / 1e-9, tn, label=r'$\tau_N$')
                            taub = ax.plot(dia / 1e-9, tb, label=r'$\tau_B$')
                            taut = ax.plot(dia / 1e-9, tau, label=r'$\tau_{total}$')
                            
                            ax.legend(loc='best')
                            ax.set_xlabel(x)
                            ax.set_ylabel(r'relaxation time $\tau$ [nm]')
                            ax.set_yscale('log')
                            ax.set_ylim(1e-9, 1e9)
                            ax.add_artist(AnchoredText(f"{Material.value} \n{Medium.value}", loc=2))
                            
                            X = np.array(dia).reshape(len(dia), 1)
                            Y = np.hstack(((np.array(tn).reshape(len(tn),1)),\
                                           (np.array(tb).reshape(len(tb),1)),\
                                           (np.array(tau).reshape(len(tau),1))))
                            Header = ['dp', 'tau_n', 'tau_b', 'tau_total']
                            export(X, Y, Material.value, Medium.value, f'{x} - {y}', Header)
                            
                    plotbutton.on_click(on_button_clicked)
                    
                elif y == 'SAR [W/g]':
                    
                    Material=wg.Text(value='Material', placeholder='Type material', disabled=False, layout=wg.Layout(width='120px', height='30px'))
                    Ku     = wg.BoundedFloatText(value=48, min=1, max=6600, step=0.1, disabled=False, layout=wg.Layout(width='100px', height='25px'))
                    Kuout  = wg.Output()
                    Medium = wg.Text(value='Medium', placeholder='Type medium', disabled=False, layout=wg.Layout(width='120px', height='30px'))
                    ds     = wg.BoundedFloatText(value=2.50, min=0, max=25, step=0.01, disabled=False, layout=wg.Layout(width='100px', height='25px'))
                    dsout  = wg.Output()
                    eta    = wg.BoundedFloatText(value=1e-3, min=1e-4, max=1e3, step=1e-4, disabled=False, layout=wg.Layout(width='100px', height='25px'))
                    etaout = wg.Output()
                    Ms     = wg.BoundedFloatText(value=1711, min=1, max=2000, step=0.1, disabled=False, layout=wg.Layout(width='100px', height='25px'))
                    Msout  = wg.Output()
                    rho    = wg.BoundedFloatText(value=7.87, min=1e-3, max=1e3, step=1e-3, disabled=False, layout=wg.Layout(width='100px', height='25px'))
                    rhoout = wg.Output()
                    
                    Mattext = wg.Label('Material :')
                    Medtext = wg.Label('Medium :')
                    Kutext  = wg.Label(r'Anisotropy constant $K_u$ [kJ/m3] :')
                    dstext  = wg.Label(r'Surfactant layer thickness $d_s$ [nm]:')
                    etatext = wg.Label(r'Viscosity $\eta$ [Ns/m2] :')
                    rhotext = wg.Label(r'Density $\rho$ [g/cm3] :')
                    Mstext  = wg.Label(r'Saturation magnetization $M_s$ [kA/m] :')

                    space  = wg.Label(r'$\quad$')
                    if x == 'Diameter dp [nm]':
                        freqtext = wg.Label('Frequency f [kHz] :', layout=wg.Layout(width='120px', height='30px'))
                        freq0 = wg.BoundedIntText(value=100, min=1, max=500, disabled=False, layout=wg.Layout(width='70px'))
                        freqout0 = wg.Output()
                        fieldtext= wg.Label('Field H [G] :', layout=wg.Layout(width='100px', height='30px'))
                        field0 = wg.BoundedIntText(value=100, min=0, max=500, disabled=False, layout=wg.Layout(width='70px'))
                        fieldout0 = wg.Output()
                        
                        plotbutton = wg.Button(description='Plot!', tooltip='Click this to plot')
                        plotbuttonout = wg.Output()

                        display(HBox((VBox((Mattext, Medtext)),
                                      VBox((Material, Medium)), space,
                                      VBox((Kutext, dstext)),
                                      VBox((Ku, Kuout, ds, dsout)), space,
                                      VBox((rhotext, etatext)),
                                      VBox((rho, rhoout, eta, etaout)), space,
                                      VBox((Mstext, space)),
                                      VBox((Ms, Msout)) )) )
                        display(HBox((freqtext, freq0, freqout0, fieldtext, field0, fieldout0, plotbutton)))
                        display(plotbuttonout)

                        def on_button_clicked(plot):
                            with plotbuttonout:
                                siKu  = float(Ku.value    * unit['Factor']['Anisotropy constant'])
                                siMs  = float(Ms.value    * unit['Factor']['Saturation magnetization'])
                                sirho = float(rho.value   * unit['Factor']['Density'])
                                sieta = float(eta.value   * unit['Factor']['Viscosity'])
                                sids  = float(ds.value    * unit['Factor']['Surfactant layer thickness'])
                                sif   = float(freq0.value * unit['Factor']['Frequency'])
                                siH   = float(field0.value* unit['Factor']['Field'])

                                maxdia = ((6 * kb * T * np.log(1e30)) / (siKu * np.pi))**(1/3) * 1e9
                                dia = np.arange(1, maxdia, 0.05) * 1e-9
#                                 tn = tau0 * np.exp((siKu * np.pi * dia**3) / (6 * kb * T))
                                tn = tau0 * ((siKu * np.pi * dia**3) / (6 * kb * T))**(-0.5) * np.exp((siKu * np.pi * dia**3) / (6 * kb * T))
                                tb = (sieta * np.pi * (dia + sids)**3) / (2 * kb * T)
                                tau = (tn * tb) / (tn + tb)

                                sartn = ((np.pi**3 * vacuumpermeability**2 * siH**2 * siMs**2 * dia**3 * sif**2 * tn) /\
                                         (9 * kb * T * sirho * (1 + (2 * np.pi * sif * tn)**2))) * 1e-3
                                sartb = ((np.pi**3 * vacuumpermeability**2 * siH**2 * siMs**2 * dia**3 * sif**2 * tb) /\
                                         (9 * kb * T * sirho * (1 + (2 * np.pi * sif * tb)**2))) * 1e-3
                                sartot = ((np.pi**3 * vacuumpermeability**2 * siH**2 * siMs**2 * dia**3 * sif**2 * tau) /\
                                          (9 * kb * T * sirho * (1 + (2 * np.pi * sif * tau)**2))) * 1e-3

                                fig, ax = plt.subplots()
                                ax.plot(dia / 1e-9, sartn, label=r'only considering $\tau_N$')
                                ax.plot(dia / 1e-9, sartb, label=r'only considering $\tau_B$')
                                ax.plot(dia / 1e-9, sartot, label=r'considering $\tau_{total}$')

                                ax.set_xlabel(x)
                                ax.set_ylabel(y)
                                ax.set_yscale('log')
                                ax.set_ylim(1e-4,1e6)
                                ax.legend(loc='upper right', fontsize=8)
                                ax.add_artist(AnchoredText(f"{Material.value} \n{Medium.value} \nf = {freq0.value} kHz \nH = {field0.value} G", loc=2))
                                
                                X = np.array(dia).reshape(len(dia), 1)
                                Y = np.hstack(((np.array(sartn).reshape(len(sartn),1)),\
                                               (np.array(sartb).reshape(len(sartb),1)),\
                                               (np.array(sartot).reshape(len(sartot),1))))
                                Header = ['dp', 'SAR_taun', 'SAR_taub', 'SAR_total']
                                export(X, Y, Material.value, Medium.value, f'{x} - {y} with f = {freq0.value} kHz, H = {field0.value} G', Header)
                        
                        plotbutton.on_click(on_button_clicked)
                    elif x == 'Frequency f [kHz]':
                        diatext = wg.Label('Diameter dp [nm] :', layout=wg.Layout(width='120px', height='30px'))
                        dia0 = wg.BoundedFloatText(value=1, min=1, max=50, step=0.01, disabled=False, layout=wg.Layout(width='70px'))
                        diaout0 = wg.Output()
                        fieldtext= wg.Label('Field H [G] :', layout=wg.Layout(width='100px', height='30px'))
                        field0 = wg.BoundedIntText(value=100, min=0, max=500, disabled=False, layout=wg.Layout(width='70px'))
                        fieldout0 = wg.Output()
                        
                        plotbutton = wg.Button(description='Plot!', tooltip='Click this to plot')
                        plotbuttonout = wg.Output()

                        display(HBox((VBox((Mattext, Medtext)),
                                      VBox((Material, Medium)), space,
                                      VBox((Kutext, dstext)),
                                      VBox((Ku, Kuout, ds, dsout)), space,
                                      VBox((rhotext, etatext)),
                                      VBox((rho, rhoout, eta, etaout)), space,
                                      VBox((Mstext, space)),
                                      VBox((Ms, Msout)) )) )
                        display(HBox((diatext, dia0, diaout0, fieldtext, field0, fieldout0, plotbutton)))
                        display(plotbuttonout)

                        def on_button_clicked(plot):
                            with plotbuttonout:
                                siKu  = float(Ku.value    * unit['Factor']['Anisotropy constant'])
                                siMs  = float(Ms.value    * unit['Factor']['Saturation magnetization'])
                                sirho = float(rho.value   * unit['Factor']['Density'])
                                sieta = float(eta.value   * unit['Factor']['Viscosity'])
                                sids  = float(ds.value    * unit['Factor']['Surfactant layer thickness'])
                                sidia = float(dia0.value  * unit['Factor']['Surfactant layer thickness'])
                                siH   = float(field0.value* unit['Factor']['Field'])

#                                 maxdia = ((6 * kb * T * np.log(1e50)) / (siKu * np.pi))**(1/3) * 1e9
#                                 dia = np.arange(1, maxdia, 0.05) * 1e-9
                                sif = np.arange(1, 500, 1) * unit['Factor']['Frequency']
                                tn = tau0 * np.exp((siKu * np.pi * sidia**3) / (6 * kb * T))
                                tb = (sieta * np.pi * (sidia + sids)**3) / (2 * kb * T)
                                tau = (tn * tb) / (tn + tb)

                                sartn = ((np.pi**3 * vacuumpermeability**2 * siH**2 * siMs**2 * sidia**3 * sif**2 * tn) /\
                                         (9 * kb * T * sirho * (1 + (2 * np.pi * sif * tn)**2))) * 1e-3
                                sartb = ((np.pi**3 * vacuumpermeability**2 * siH**2 * siMs**2 * sidia**3 * sif**2 * tb) /\
                                         (9 * kb * T * sirho * (1 + (2 * np.pi * sif * tb)**2))) * 1e-3
                                sartot = ((np.pi**3 * vacuumpermeability**2 * siH**2 * siMs**2 * sidia**3 * sif**2 * tau) /\
                                          (9 * kb * T * sirho * (1 + (2 * np.pi * sif * tau)**2))) * 1e-3

                                fig, ax = plt.subplots()
                                ax.plot(sif / unit['Factor']['Frequency'], sartn, label=r'only considering $\tau_N$')
                                ax.plot(sif / unit['Factor']['Frequency'], sartb, label=r'only considering $\tau_B$')
                                ax.plot(sif / unit['Factor']['Frequency'], sartot, label=r'considering $\tau_{total}$')

                                ax.set_xlabel(x)
                                ax.set_ylabel(y)
#                                 ax.set_yscale('log')
#                                 ax.set_ylim(1e-4,1e6)
                                ax.legend(loc='upper right', fontsize=8)
                                ax.add_artist(AnchoredText(f"{Material.value} \n{Medium.value} \ndp = {dia0.value} nm \nH = {field0.value} G", loc=2))
                                
                                X = np.array(sif).reshape(len(sif), 1)
                                Y = np.hstack(((np.array(sartn).reshape(len(sartn),1)),\
                                               (np.array(sartb).reshape(len(sartb),1)),\
                                               (np.array(sartot).reshape(len(sartot),1))))
                                Header = ['f', 'SAR_taun', 'SAR_taub', 'SAR_total']
                                export(X, Y, Material.value, Medium.value, f'{x} - {y} with dp = {dia0.value} nm, H = {field0.value} G', Header)
                        
                        plotbutton.on_click(on_button_clicked)
                    elif x == 'Field H [G]':
                        diatext = wg.Label('Diameter dp [nm] :', layout=wg.Layout(width='120px', height='30px'))
                        dia0 = wg.BoundedFloatText(value=1, min=1, max=50, step=0.01, disabled=False, layout=wg.Layout(width='70px'))
                        diaout0 = wg.Output()
                        freqtext= wg.Label('Frequency f [G] :', layout=wg.Layout(width='120px', height='30px'))
                        freq0 = wg.BoundedIntText(value=100, min=0, max=500, disabled=False, layout=wg.Layout(width='70px'))
                        freqout0 = wg.Output()
                        
                        plotbutton = wg.Button(description='Plot!', tooltip='Click this to plot')
                        plotbuttonout = wg.Output()

                        display(HBox((VBox((Mattext, Medtext)),
                                      VBox((Material, Medium)), space,
                                      VBox((Kutext, dstext)),
                                      VBox((Ku, Kuout, ds, dsout)), space,
                                      VBox((rhotext, etatext)),
                                      VBox((rho, rhoout, eta, etaout)), space,
                                      VBox((Mstext, space)),
                                      VBox((Ms, Msout)) )) )
                        display(HBox((diatext, dia0, diaout0, freqtext, freq0, freqout0, plotbutton)))
                        display(plotbuttonout)

                        def on_button_clicked(plot):
                            with plotbuttonout:
                                siKu  = float(Ku.value    * unit['Factor']['Anisotropy constant'])
                                siMs  = float(Ms.value    * unit['Factor']['Saturation magnetization'])
                                sirho = float(rho.value   * unit['Factor']['Density'])
                                sieta = float(eta.value   * unit['Factor']['Viscosity'])
                                sids  = float(ds.value    * unit['Factor']['Surfactant layer thickness'])
                                sidia = float(dia0.value  * unit['Factor']['Surfactant layer thickness'])
                                sif   = float(freq0.value* unit['Factor']['Frequency'])

                                siH = np.arange(1, 500, 1) * unit['Factor']['Field']
                                
                                tn = tau0 * ((siKu * np.pi * sidia**3) / (6 * kb * T))**(-0.5) * np.exp((siKu * np.pi * sidia**3) / (6 * kb * T))
                                tb = (sieta * np.pi * (sidia + sids)**3) / (2 * kb * T)
                                tau = (tn * tb) / (tn + tb)

                                sartn = ((np.pi**3 * vacuumpermeability**2 * siH**2 * siMs**2 * sidia**3 * sif**2 * tn) /\
                                         (9 * kb * T * sirho * (1 + (2 * np.pi * sif * tn)**2))) * 1e-3
                                sartb = ((np.pi**3 * vacuumpermeability**2 * siH**2 * siMs**2 * sidia**3 * sif**2 * tb) /\
                                         (9 * kb * T * sirho * (1 + (2 * np.pi * sif * tb)**2))) * 1e-3
                                sartot = ((np.pi**3 * vacuumpermeability**2 * siH**2 * siMs**2 * sidia**3 * sif**2 * tau) /\
                                          (9 * kb * T * sirho * (1 + (2 * np.pi * sif * tau)**2))) * 1e-3

                                fig, ax = plt.subplots()
                                ax.plot(siH / unit['Factor']['Field'], sartn, label=r'only considering $\tau_N$')
                                ax.plot(siH / unit['Factor']['Field'], sartb, label=r'only considering $\tau_B$')
                                ax.plot(siH / unit['Factor']['Field'], sartot, label=r'considering $\tau_{total}$')

                                ax.set_xlabel(x)
                                ax.set_ylabel(y)
                                ax.legend(loc='upper right', fontsize=8)
                                ax.add_artist(AnchoredText(f"{Material.value} \n{Medium.value} \ndp = {dia0.value} nm \nf = {freq0.value} kHz", loc=2))
                                
                                X = np.array(siH).reshape(len(siH), 1)
                                Y = np.hstack(((np.array(sartn).reshape(len(sartn),1)),\
                                               (np.array(sartb).reshape(len(sartb),1)),\
                                               (np.array(sartot).reshape(len(sartot),1))))
                                Header = ['H', 'SAR_taun', 'SAR_taub', 'SAR_total']
                                export(X, Y, Material.value, Medium.value, f'{x} - {y} with dp = {dia0.value} nm, f = {freq0.value} kHz', Header)
                        
                        plotbutton.on_click(on_button_clicked)
                        
                    
            wg.interact(choosey, y=optiony)
        wg.interact(choosex, x=['select x', 'Diameter dp [nm]', 'Frequency f [kHz]', 'Field H [G]'])
    
    ##########################################################################################################################################################
    
    if dim == '3D':
        display(wg.Label(r'High viscosity medium is assumed, thus, ignoring the influence of Brownian relaxation $\tau_B$ in heat generation mechanism.'))
        Material = wg.Text(value='Material', placeholder='Type material', disabled=False, layout=wg.Layout(width='100px', height='25px'))
        Ku     = wg.BoundedFloatText(value=48, min=1, max=6600, step=0.1, disabled=False, layout=wg.Layout(width='100px', height='25px'))
        Kuout  = wg.Output()
        Ms     = wg.BoundedFloatText(value=1711, min=1, max=2000, step=0.1, disabled=False, layout=wg.Layout(width='100px', height='25px'))
        Msout  = wg.Output()
        rho    = wg.BoundedFloatText(value=7.87, min=1e-3, max=1e3, step=1e-3, disabled=False, layout=wg.Layout(width='100px', height='25px'))
        rhoout = wg.Output()

        Mattext = wg.Label('Material :')
        Kutext  = wg.Label(r'Anisotropy constant $K_u$ [kJ/m3] :')
        Mstext  = wg.Label(r'Saturation magnetization $M_s$ [kA/m] :')
        rhotext = wg.Label(r'Density $\rho$ [g/cm3] :')
        
        space  = wg.Label(r'$\,$')
        
        display(HBox((VBox((Mattext, rhotext)),
                      VBox((Material, rho, rhoout)),
                      space,
                      VBox((Kutext, Mstext)),
                      VBox((Ku, Kuout, Ms, Msout)) )) )
        diastep = 0.05
        def choosex(x):
            if x == 'select x':
                optiony = ['select x']
            elif x == 'Frequency f [kHz]':
                freq = np.arange(1, 501, 1)
                xx = freq * unit['Factor']['Frequency']
                optiony = ['select y', 'Field H [G]', 'Diameter dp [nm]']
            elif x == 'Field H [G]':
                fields = np.arange(1, 501, 1)
                xx = fields * unit['Factor']['Field']
                optiony = ['select y', 'Frequency f [kHz]', 'Diameter dp [nm]']
            elif x == 'Diameter dp [nm]':
                optiony = ['select y', 'Frequency f [kHz]', 'Field H [G]']
            
            def choosey(y):
                if y == 'select x':
                    optionz = ['select x']
                elif y == 'select y':
                    optionz = ['select y']
                elif y == 'Frequency f [kHz]':
                    freq = np.arange(1, 501, 1)
                    yy = freq * unit['Factor']['Frequency']
                    optionz = ['select z', 'SAR [W/g]']
                elif y == 'Field H [G]':
                    fields = np.arange(1, 501, 1)
                    yy = fields * unit['Factor']['Field']
                    optionz = ['select z', 'SAR [W/g]']
                elif y == 'Diameter dp [nm]':
                    optionz = ['select z', 'SAR [W/g]']
                
                def choosez(z):
                    if z == 'SAR [W/g]':
                        if (x == 'Frequency f [kHz]' and y == 'Field H [G]') or\
                           (y == 'Frequency f [kHz]' and x == 'Field H [G]'):
                            diatext = wg.Label('Diameter dp [nm] :', layout=wg.Layout(width='120px', height='30px'))
                            dia0 = wg.BoundedFloatText(value=10, min=1, max=60, step=0.01, disabled=False, layout=wg.Layout(width='100px', height='25px'))
                            diaout0 = wg.Output()
                            plotbutton = wg.Button(description='Plot!', tooltip='Click this to plot')
                            plotbuttonout = wg.Output()
                            display(HBox((diatext, dia0, diaout0, plotbutton)) )
                            display(plotbuttonout)
                            def on_button_clicked(plot):
                                with plotbuttonout:
                                    siKu  = float(Ku.value   * unit['Factor']['Anisotropy constant'])
                                    siMs  = float(Ms.value   * unit['Factor']['Saturation magnetization'])
                                    sirho = float(rho.value  * unit['Factor']['Density'])
                                    sidia = float(dia0.value * 1e-9)
                
                                    X = xx
                                    Y = yy
                                    X, Y = np.meshgrid(X, Y)
                                    maxdia = ((6 * kb * T * np.log(1e30)) / (siKu * np.pi))**(1/3)
                                    if sidia >= maxdia:
                                        print(f'exp factor reached 1e50. Max accepted diameter is {round(maxdia * 1e9, 2)} nm')
                                    else:
                                        fig = plt.figure()
                                        ax = fig.gca(projection='3d')
                                        plt.tight_layout()
                                        ax.set_xlabel(x)
                                        ax.set_ylabel(y)
                                        ax.set_zlabel(z)
                                        ax.invert_yaxis()
#                                         ax.view_init(elev=16, azim=40)
#                                         ax.view_init(elev=13, azim=-134)
                                        ax.view_init(elev=18, azim=-27)
                                        ax.text2D(0.0, 0.98, f"{Material.value}", transform=ax.transAxes)
                                        ax.text2D(0.0, 0.94, f"Ms: {Ms.value} kA/m, Ku: {Ku.value} kJ/m3, rho: {rho.value} g/cm3", transform=ax.transAxes, fontsize=8)
                                        ax.text2D(0.0, 0.90, f"Particle diameter: {dia0.value} nm", transform=ax.transAxes, fontsize=8)
#                                         tau = tau0 * np.exp((siKu * np.pi * sidia**3) / (6 * kb * T))
                                        tau = tau0 * ((siKu * np.pi * sidia**3) / (6 * kb * T))**(-0.5) * np.exp((siKu * np.pi * sidia**3) / (6 * kb * T))
                                        if x == 'Frequency f [kHz]':
                                            sar = ((np.pi**3 * vacuumpermeability**2 * Y**2 * siMs**2 * sidia**3 * X**2 * tau) /\
                                                  (9 * kb * T * sirho * (1 + (2 * np.pi * X * tau)**2))) * 1e-3
                                            surf = ax.plot_surface(X / unit['Factor']['Frequency'], Y / unit['Factor']['Field'], sar, cmap=cm.jet)
                                        else:
                                            sar = ((np.pi**3 * vacuumpermeability**2 * X**2 * siMs**2 * sidia**3 * Y**2 * tau) /\
                                                  (9 * kb * T * sirho * (1 + (2 * np.pi * Y * tau)**2))) * 1e-3
                                            surf = ax.plot_surface(X / unit['Factor']['Field'], Y / unit['Factor']['Frequency'], sar, cmap=cm.jet)                                 
                                        
                                        XYexport = np.hstack((np.array(X).reshape(np.shape(X)[0] * np.shape(X)[1], 1), np.array(Y).reshape(np.shape(Y)[0] * np.shape(Y)[1], 1)))
                                        Zexport = np.hstack((np.array(sar).reshape(np.shape(sar)[0] * np.shape(sar)[1], 1), np.array(sar).reshape(np.shape(sar)[0] * np.shape(sar)[1], 1)))
                                        Header = [x, y, z, z]
                                        export(XYexport, Zexport, Material.value, None, f"{x} - {y} - {z} with dp: {dia0.value} nm", Header)
                                        
                            plotbutton.on_click(on_button_clicked)
                            
                        elif (x == 'Frequency f [kHz]' and y == 'Diameter dp [nm]') or\
                             (y == 'Frequency f [kHz]' and x == 'Diameter dp [nm]'):
                            
                            fieldtext = wg.Label('Field H [G] :', layout=wg.Layout(width='120px', height='30px'))
                            field0 = wg.BoundedIntText(value=100, min=1, max=500, disabled=False, layout=wg.Layout(width='70px'))
                            fieldout0 = wg.Output()
                            plotbutton = wg.Button(description='Plot!', tooltip='Click this to plot')
                            plotbuttonout = wg.Output()
                            display(HBox((fieldtext, field0, fieldout0, plotbutton)) )
                            display(plotbuttonout)
                            def on_button_clicked(plot):
                                with plotbuttonout:
                                    siKu  = float(Ku.value     * unit['Factor']['Anisotropy constant'])
                                    siMs  = float(Ms.value     * unit['Factor']['Saturation magnetization'])
                                    sirho = float(rho.value    * unit['Factor']['Density'])
                                    siH   = float(field0.value * unit['Factor']['Field'])
                
                                    fig = plt.figure()
                                    ax = fig.gca(projection='3d')
                                    plt.tight_layout()
                                    ax.set_xlabel(x)
                                    ax.set_ylabel(y)
                                    ax.set_zlabel(z)
                                    ax.invert_xaxis()
#                                     ax.view_init(elev=16, azim=40)
#                                     ax.view_init(elev=13, azim=-134)
                                    ax.view_init(elev=18, azim=-27)
                                    ax.text2D(0.0, 0.98, f"{Material.value}", transform=ax.transAxes)
                                    ax.text2D(0.0, 0.94, f"Ms: {Ms.value} kA/m, Ku: {Ku.value} kJ/m3, rho: {rho.value} g/cm3", transform=ax.transAxes, fontsize=8)
                                    ax.text2D(0.0, 0.90, f"Field: {field0.value} G", transform=ax.transAxes, fontsize=8)
                                    if x == 'Frequency f [kHz]':
                                        X = xx
                                        maxdia = ((6 * kb * T * np.log(1e50)) / (siKu * np.pi))**(1/3) * 1e9
                                        Y = np.arange(1, maxdia, diastep) * 1e-9
                                        X, Y = np.meshgrid(X, Y)
                                        tau = tau0 * ((siKu * np.pi * Y**3) / (6 * kb * T))**(-0.5) * np.exp((siKu * np.pi * Y**3) / (6 * kb * T))
                                        sar = ((np.pi**3 * vacuumpermeability**2 * siH**2 * siMs**2 * Y**3 * X**2 * tau) /\
                                              (9 * kb * T * sirho * (1 + (2 * np.pi * X * tau)**2))) * 1e-3
                                        surf = ax.plot_surface(X / unit['Factor']['Frequency'], Y / 1e-9, sar, cmap=cm.jet, linewidth=5, antialiased=False, rstride=1, cstride=1)
                                    else:
                                        Y = yy
                                        maxdia = ((6 * kb * T * np.log(1e50)) / (siKu * np.pi))**(1/3) * 1e9
                                        X = np.arange(1, maxdia, diastep) * 1e-9
                                        X, Y = np.meshgrid(X, Y)
#                                         tau = tau0 * np.exp((siKu * np.pi * X**3) / (6 * kb * T))
                                        tau = tau0 * ((siKu * np.pi * X**3) / (6 * kb * T))**(-0.5) * np.exp((siKu * np.pi * X**3) / (6 * kb * T))
                                        sar = ((np.pi**3 * vacuumpermeability**2 * siH**2 * siMs**2 * X**3 * Y**2 * tau) /\
                                              (9 * kb * T * sirho * (1 + (2 * np.pi * Y * tau)**2))) * 1e-3
                                        surf = ax.plot_surface(X / 1e-9, Y / unit['Factor']['Frequency'], sar, cmap=cm.jet, linewidth=5, antialiased=False, rstride=1, cstride=1)
                                    XYexport = np.hstack((np.array(X).reshape(np.shape(X)[0] * np.shape(X)[1], 1), np.array(Y).reshape(np.shape(Y)[0] * np.shape(Y)[1], 1)))
                                    Zexport = np.hstack((np.array(sar).reshape(np.shape(sar)[0] * np.shape(sar)[1], 1), np.array(sar).reshape(np.shape(sar)[0] * np.shape(sar)[1], 1)))
                                    Header = [x, y, z, z]
                                    export(XYexport, Zexport, Material.value, None, f"{x} - {y} - {z} with H: {field0.value} G", Header)
                            plotbutton.on_click(on_button_clicked)
                            
                        elif (x == 'Field H [G]' and y == 'Diameter dp [nm]') or\
                             (y == 'Field H [G]' and x == 'Diameter dp [nm]'):
                            
                            freqtext = wg.Label('Frequency f [kHz] :', layout=wg.Layout(width='120px', height='30px'))
                            freq0 = wg.BoundedIntText(value=100, min=1, max=500, disabled=False, layout=wg.Layout(width='70px'))
                            freqout0 = wg.Output()
                            plotbutton = wg.Button(description='Plot!', tooltip='Click this to plot')
                            plotbuttonout = wg.Output()
                            display(HBox((freqtext, freq0, freqout0, plotbutton)) )
                            display(plotbuttonout)
                            def on_button_clicked(plot):
                                with plotbuttonout:
                                    siKu  = float(Ku.value     * unit['Factor']['Anisotropy constant'])
                                    siMs  = float(Ms.value     * unit['Factor']['Saturation magnetization'])
                                    sirho = float(rho.value    * unit['Factor']['Density'])
                                    sif   = float(freq0.value * unit['Factor']['Frequency'])
                                    
                                    fig = plt.figure()
                                    ax = fig.gca(projection='3d')
                                    plt.tight_layout()
                                    ax.set_xlabel(x)
                                    ax.set_ylabel(y)
                                    ax.set_zlabel(z)
                                    ax.invert_xaxis()
#                                     ax.view_init(elev=16, azim=40)
#                                     ax.view_init(elev=13, azim=-134)
                                    ax.view_init(elev=18, azim=-27)
                                    ax.text2D(0.0, 0.98, f"{Material.value}", transform=ax.transAxes)
                                    ax.text2D(0.0, 0.94, f"Ms: {Ms.value} kA/m, Ku: {Ku.value} kJ/m3, rho: {rho.value} g/cm3", transform=ax.transAxes, fontsize=8)
                                    ax.text2D(0.0, 0.90, f"Frequency: {freq0.value} kHz", transform=ax.transAxes, fontsize=8)
                                    if x == 'Field H [G]':
                                        X = xx
                                        maxdia = ((6 * kb * T * np.log(1e50)) / (siKu * np.pi))**(1/3) * 1e9
                                        Y = np.arange(1, maxdia, diastep) * 1e-9
                                        X, Y = np.meshgrid(X, Y)
#                                         tau = tau0 * np.exp((siKu * np.pi * Y**3) / (6 * kb * T))
                                        tau = tau0 * ((siKu * np.pi * Y**3) / (6 * kb * T))**(-0.5) * np.exp((siKu * np.pi * Y**3) / (6 * kb * T))
                                        sar = ((np.pi**3 * vacuumpermeability**2 * X**2 * siMs**2 * Y**3 * sif**2 * tau) /\
                                              (9 * kb * T * sirho * (1 + (2 * np.pi * sif * tau)**2))) * 1e-3
                                        surf = ax.plot_surface(X / unit['Factor']['Field'], Y / 1e-9, sar, cmap=cm.jet, linewidth=5, antialiased=False, rstride=1, cstride=1)
                                    else:
                                        Y = yy
                                        maxdia = ((6 * kb * T * np.log(1e50)) / (siKu * np.pi))**(1/3) * 1e9
                                        X = np.arange(1, maxdia, diastep) * 1e-9
                                        X, Y = np.meshgrid(X, Y)
#                                         tau = tau0 * np.exp((siKu * np.pi * X**3) / (6 * kb * T))
                                        tau = tau0 * ((siKu * np.pi * X**3) / (6 * kb * T))**(-0.5) * np.exp((siKu * np.pi * X**3) / (6 * kb * T))
                                        sar = ((np.pi**3 * vacuumpermeability**2 * Y**2 * siMs**2 * X**3 * sif**2 * tau) /\
                                              (9 * kb * T * sirho * (1 + (2 * np.pi * sif * tau)**2))) * 1e-3
                                        surf = ax.plot_surface(X / 1e-9, Y / unit['Factor']['Field'], sar, cmap=cm.jet, linewidth=5, antialiased=False, rstride=1, cstride=1)                                 
                                    XYexport = np.hstack((np.array(X).reshape(np.shape(X)[0] * np.shape(X)[1], 1), np.array(Y).reshape(np.shape(Y)[0] * np.shape(Y)[1], 1)))
                                    Zexport = np.hstack((np.array(sar).reshape(np.shape(sar)[0] * np.shape(sar)[1], 1), np.array(sar).reshape(np.shape(sar)[0] * np.shape(sar)[1], 1)))
                                    Header = [x, y, z, z]
                                    export(XYexport, Zexport, Material.value, None, f"{x} - {y} - {z} with f: {freq0.value} kHz", Header)
                            plotbutton.on_click(on_button_clicked)
                        
                wg.interact(choosez, z=optionz)
            wg.interact(choosey, y=optiony)
        wg.interact(choosex, x=['select x', 'Frequency f [kHz]','Field H [G]', 'Diameter dp [nm]'])
wg.interact(plotanything, dim=['2D', '3D'])



interactive(children=(Dropdown(description='dim', options=('2D', '3D'), value='2D'), Output()), _dom_classes=(…

<function __main__.plotanything(dim)>

In [8]:
# a = np.arange(0,9,1)
# b = np.arange(1,5,1)
# a, b = np.meshgrid(a, b)
# print(a, np.shape(a))
# print(b, np.shape(b))